In [13]:
import csv
from pyspark import SparkContext, SparkConf
from pyspark.mllib.stat import Statistics

In [ ]:
conf = SparkConf().setAppName('ListenerSummarizer')
sc = SparkContext(conf=conf)

In [14]:
trackfile = sc.textFile('tracks.csv')

def make_tracks_kv(str):
	l = str.split(",")
	return [l[1], [[int(l[2]), l[3], int(l[4]), l[5]]]]

def compute_stats_byuser(tracks):
	mcount = morn = aft = eve = night = 0
	tracklist = []
	for t in tracks:
		trackid, dtime, mobile, zip = t
		if trackid not in tracklist:
			tracklist.append(trackid)
		d, t = dtime.split(" ")
		hourofday = int(t.split(":")[0])
		mcount += mobile
		if (hourofday < 5):
			night += 1
		elif (hourofday < 12):
			morn += 1
		elif (hourofday < 17):
			aft += 1
		elif (hourofday < 22):
			eve += 1
		else:
			night += 1
	return [len(tracklist), morn, aft, eve, night, mcount]


In [15]:
tbycust = trackfile.map(lambda line: make_tracks_kv(line)).reduceByKey(lambda a, b: a + b)
tbycust.first()

('48',
 [[453, '"2014-10-23 03:26:20"', 0, '"72132"'],
  [81, '"2014-11-06 07:13:59"', 0, '"56726"'],
  [245, '"2014-10-09 18:36:15"', 1, '"85378"'],
  [15, '"2014-11-28 08:22:58"', 0, '"20097"'],
  [532, '"2014-11-27 04:18:24"', 0, '"93555"'],
  [1360, '"2014-12-27 12:53:31"', 0, '"06491"'],
  [1274, '"2014-12-12 11:26:47"', 1, '"02458"'],
  [1499, '"2014-10-17 09:35:47"', 0, '"31625"'],
  [1326, '"2014-10-08 03:36:44"', 0, '"60913"'],
  [5, '"2014-12-12 17:17:47"', 0, '"68956"'],
  [1586, '"2014-10-09 14:23:26"', 1, '"07801"'],
  [601, '"2014-10-26 19:11:48"', 0, '"55807"'],
  [189, '"2014-11-23 22:01:55"', 1, '"49006"'],
  [551, '"2014-11-30 03:47:51"', 0, '"56347"'],
  [456, '"2014-12-21 22:31:23"', 1, '"35979"'],
  [640, '"2014-11-09 10:37:51"', 0, '"07405"'],
  [909, '"2014-11-24 01:59:47"', 1, '"98223"'],
  [981, '"2014-12-30 03:00:31"', 0, '"79018"'],
  [173, '"2014-12-27 10:29:45"', 0, '"64061"'],
  [263, '"2014-10-31 15:57:54"', 1, '"24090"'],
  [82, '"2014-12-05 12:46:47"', 

In [20]:
custdata = tbycust.mapValues(lambda a: compute_stats_byuser(a))
custdata.take(5)

[('48', [696, 310, 217, 223, 277, 503]),
 ('1081', [201, 61, 53, 42, 73, 166]),
 ('2641', [128, 35, 38, 23, 40, 101]),
 ('1811', [142, 53, 34, 32, 41, 121]),
 ('2932', [133, 33, 39, 31, 42, 63])]

In [18]:
aggdata = Statistics.colStats(custdata.map(lambda x: x[1]))
aggdata.mean()

array([170.295 ,  58.2908,  41.6434,  41.7626,  58.3032, 121.553 ])

In [19]:
aggdata.variance()

array([13699.38585217,  4542.28029142,  2292.05224689,  2305.31570438,
        4525.56558288, 22140.06240348])